In [1]:
# Notebook matches outbreak names in the extractions corresponding to the same outbreak
# Import packages and set OPENAI Key access
import nltk
import json
#import langchain as lc
from getpass import getpass 
import os
os.chdir('..')
from langchain.chat_models import ChatOpenAI
from langchain.embeddings import OpenAIEmbeddings
import tiktoken
import pdb
import numpy as np
#from langchain.chains import create_extraction_chain
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage
)
PROMED_DIR = os.path.join('..','WHO_DON','Data','ProMED')
WHO_DIR = os.path.join('..','WHO_DON','Data','WHO DON')
OPENAI_API_KEY = os.environ['OPENAI_API_KEY']
OPENAI_ORGANIZATION = os.environ['OPENAI_ORGANIZATION']
chatGPT4 = ChatOpenAI(openai_api_key=OPENAI_API_KEY, openai_organization= OPENAI_ORGANIZATION, temperature=0, model="gpt-4")
chatGPT35 = ChatOpenAI(openai_api_key=OPENAI_API_KEY, openai_organization= OPENAI_ORGANIZATION, temperature=0, model="gpt-3.5-turbo")
embeddings = OpenAIEmbeddings(
    model="text-embedding-ada-002",
    openai_api_key=OPENAI_API_KEY, 
    openai_organization= OPENAI_ORGANIZATION
)
encoding = tiktoken.encoding_for_model("gpt-3.5-turbo")

In [2]:
# Rushali did prompt engineering to process the ~65000 headers in batch (perhaps 10-50 in one query).
# Outbreak names and countries were extracted from the LLM. Dates were extracted by parsing
# ID should correspond to the index in the ProMed data read sequentially from file 1 to 13.
# The results are in the extractions below.
Extr = json.load(open('promed.json'))
ix =14681
print('Keys:', list(Extr.keys()))
print('ID:', Extr['ID'][str(ix)])
print('outbreakName:', Extr['outbreakName'][str(ix)])
print('outbreakNameStd:', Extr['outbreakNameStd'][str(ix)])
print('countries:', Extr['countries'][str(ix)])
print('states:', Extr['states'][str(ix)])
print('datePublished:', Extr['datePublished'][str(ix)])
#print(PMedRaw[ix]['header'])

Keys: ['ID', 'archiveNumber', 'outbreakName', 'outbreakNameStd', 'countries', 'states', 'datePublished']
ID: 14681
outbreakName: Eastern equine encephalitis
outbreakNameStd: None
countries: Colombia
states: None
datePublished: None


In [3]:
# Convert Extr to a dataframe. Also convert dates from string to date objects.
from dateutil import parser
from dateutil.tz import gettz
import numpy as np
import pandas as pd
dct = {k:list(kv.values()) for k,kv in Extr.items()}
df = pd.DataFrame(dct)
ix = df[df['datePublished'].isna()].index
df.drop(ix, inplace=True)
dates = []
tzinfos = {"EDT": gettz("America/New_York"), "EST": gettz("America/New_York")}
# def str2Date(d): 
#     parser.parse(d)
df['datePublished']= [parser.parse(d) for d in df['datePublished']]
df['outbreakName'] = [ob.strip() for ob in df['outbreakName']]
df

/Users/shajain/miniforge3/lib/python3.9/site-packages/dateutil/parser/_parser.py:1207: UnknownTimezoneWarning: tzname EDT identified but not understood.  Pass `tzinfos` argument in order to correctly return a timezone-aware datetime.  In a future version, this will raise an exception.
  warnings.warn("tzname {tzname} identified but not understood.  "
/Users/shajain/miniforge3/lib/python3.9/site-packages/dateutil/parser/_parser.py:1207: UnknownTimezoneWarning: tzname EST identified but not understood.  Pass `tzinfos` argument in order to correctly return a timezone-aware datetime.  In a future version, this will raise an exception.
  warnings.warn("tzname {tzname} identified but not understood.  "


ID     archiveNumber        outbreakName outbreakNameStd  \
0          0     20070321.1000     Avian influenza            None   
1          1  20210909.8656968           Tularemia            None   
2          2  20130905.1925275  American foulbrood            None   
3          3  20210509.8352882    COVID-19, dengue            None   
4          4  20160428.4189378  Lumpy skin disease            None   
...      ...               ...                 ...             ...   
64539  64539     20011222.3089       Fusarium Wilt            None   
64540  64540  20191019.6736569                 Nil            None   
64541  64541  20210309.8235917        Yellow Fever            None   
64542  64542  20150110.3083730     Avian Influenza            None   
64543  64543  20141025.2891152   Vibrio vulnificus            None   

                       countries states       datePublished  
0                Kuwait, Myanmar   None 2007-03-21 18:00:01  
1                         Taiwan   None 2021-09-09 11:06:42  
2                           Fiji   None 2013-09-05 08:21:12  
3                     USA, Japan   None 2021-05-09 18:10:38  
4                       Bulgaria   None 2016-04-28 16:59:45  
...                          ...    ...                 ...  
64539   United States of America   None 2001-12-22 18:50:00  
64540   United States of America   None 2019-10-19 19:09:53  
64541                     Brazil   None 2021-03-09 01:12:54  
64542                    Nigeria   None 2015-01-10 08:39:35  
64543   United States of America   None 2014-10-24 23:17:23  

[64543 rows x 7 columns]

In [4]:
# unique outbreak names in the extractions are in obSet. ob2Names is a dictionary mapping 
# extraction of an outbreak to a list of all names it is known by. The list may include the
# name of the causing pathogen. Each list is initialized to be empty. It will will be 
# populated next using LLM 
obSet = set(df['outbreakName'])
print('number of unique Outbreaks: ' + str(len(obSet)))
print(obSet)
ob2Names = {ob:[] for ob in obSet}
# Caution: Run the code below if ob2Names is not populated by querying the LLM yet. 
# Otherwise it will delete the saved results from the LLM.
# with open('ob2Names.json' 'w') as f:
#     json.dump(ob2Names, f)

number of unique Outbreaks: 5223
{'Die-off, bald eagle', 'COVID-19, omicron', 'Acute hemorrhagic fever syndrome', "Legionnaire's Disease", 'Avian influenza (HPAI H5N6)', 'Fish die-off', 'Fig mosaic virus', 'CJD, familial', 'E. coli, toxigenic, waterborne', 'Contaminated pet food', 'Unexplained rash illness', 'Chemical exposure', 'Multiple sclerosis', 'Plague', 'HFMD-related deaths', 'Soybean cyst nematodes', 'Enterobacter cloacae', 'Monkeypox virus', 'Encephalitis', 'Cercospora Leaf Spot', 'Marburg virus disease', 'Feline pancytopenia', 'Epizootic hemorrhagic disease, deer', 'CJD (new variant), blood transfusion', 'Reverse zoonosis', 'Tick-borne disease', 'Blast, undiagnosed rust', 'Ratoon stunt', 'Febrile Illness', 'Dropsy epidemic', 'Poxvirus', 'Yellow fever vaccine efficacy', 'Chromium poisoning', 'Eastern Equine encephalitis', 'Undiagnosed die-off, fish', 'Foodborne illness, C. perfringens', 'Theileria, cattle', 'Hemorrhagic pneumonia', 'Feed poisoning', 'Ecstasy, adulterated', 'Ga

In [5]:
# Caution: Running this code may cost $$$. 
# ob2Names is a dictionary mapping extraction of an outbreak to a list of all names it is 
# known by. The list may include the name of the causing pathogen.
# The code below populates uses LLM for populating the ob2Names. It assumes that
# a file ob2Names.json is present in the current directory. ob2Names.json contains a ob2Names 
# dictionary described in the cell above. It only queries those outbreak 
# keys in ob2Names where the corresponding value is an empty list. This prevents querying 
# LLMs on the keys it has already been used on.

with open('ob2Names.json', 'r') as f:
    ob2Names = json.load(f)
    
j = 0
i = 0
for (k,v) in ob2Names.items():
    if j>2000:
        break
    
    if type(v) is list and len(v)==0:
        print(k)out = chatGPT4([HumanMessage(content= 'If the term ' + k + ' describes a specific outbreak name, ' +
                                             ' an infectious disease or a pathogen associated with an infectious disease'
                                         'give all scientific and common names for it as single json list. Also include the scientific name '+
                                        'of the causative pathogen, if and only if it exist. ' +
                                        'If ' + k + ' represents multiple outbreaks or multiple infectious dieases or ' +
                                        ' multiple pathogens, then output a json list containing "None". ' + 
                                        'Give answer only, without explanations. ' + 
                                        'Use a single json list, not a dictionary. Limit the list to a maximum size of 10.'  )])    
        
        try:
            obj = json.loads(out.content)
        #pdb.set_trace()
        except ValueError:
            obj = out.content
        ob2Names[k]= obj 
        print(obj)
        j = j + 1
        if j%10 == 0:
            # Save 10 LLM queries at a time
            with open('ob2Names.json', 'w') as f:
                json.dump(ob2Names, f)
    else:
        print(k, ' processed', i)
        i = i + 1
        #break       
        
with open('ob2Names.json', 'w') as f:
    json.dump(ob2Names, f)    

Black pod, cocoa  processed 0
Bacillus cereus, anthrax-like infection  processed 1
Trichomonosis  processed 2
Blast & sheath blight, rice  processed 3
Citrus bent leaf viroid  processed 4
E. coli infection  processed 5
Foot & Mouth Disease  processed 6
Konzo  processed 7
Ibuprofen, ethylene glycol poisoning  processed 8
Anthrax vaccine safety & efficacy  processed 9
Necrotizing fasciitis  processed 10
Hemorrhagic septicemia, cattle  processed 11
Ectromelia virus  processed 12
Fish die-off, fish  processed 13
Black water, unknown cause  processed 14
Sarcocystic neurona  processed 15
Marafivirus  processed 16
Pale cyst nematode  processed 17
Undiagnosed deaths, canine  processed 18
Parvovirus  processed 19
Human enterovirus  processed 20
Bunch rot  processed 21
Cholera, diarrhea & dysentery update  processed 22
Anthrax,human  processed 23
Golden cyst nematode, potato  processed 24
Hepatitis C  processed 25
Avian influenza, human (H9N2)  processed 26
American foul brood, apiary  processed

In [6]:
# extractions that are not outbreaks or represent multiple outbreaks are mapped to ['None'] 
# or a dictionary.
from data.stringAlignment import removeExtraneous
ob2Names2 = removeExtraneous(ob2Names)
ix=[ob not in ob2Names2 for ob in obSet]
for i in np.where(ix)[0]:
    print(list(obSet)[i],':', ob2Names[list(obSet)[i]])

Die-off, bald eagle : ['None']
Acute hemorrhagic fever syndrome : ['None']
Fish die-off : ['None']
Contaminated pet food : ['None']
Unexplained rash illness : ['None']
Chemical exposure : ['None']
Multiple sclerosis : ['None']
Feline pancytopenia : ['None']
Reverse zoonosis : ['None']
Tick-borne disease : ['None']
Blast, undiagnosed rust : ['None']
Febrile Illness : ['None']
Dropsy epidemic : None
Yellow fever vaccine efficacy : None
Chromium poisoning : ['None']
Undiagnosed die-off, fish : ['None']
Hemorrhagic pneumonia : ['None']
Feed poisoning : ['None']
Ecstasy, adulterated : ['None']
Undiagnosed disease, coconut palm : ['None']
Body piercing, tatooing & infection : ['None']
Palytoxin : ['None']
Tomato viruses : ['None']
Antimicrobial resistant bacteria : ['None']
Undiagnosed disease, bovine : ['None']
Inflammatory bowel disease, cytomegalovirus : ['None']
Thread blight : None
Paget's disease : ['None']
Hemorrhagic disease : ['None']
Undiagnosed die-off, marine wildlife : ['None']


Hepatitis, undefined, adenovirus associated : ['None']
Poisoning, mushrooms : ['None']
Purple blotch & anthracnose : ['None']
Undiagnosed mortality, caprine : ['None']
Blast : ['None']
P4 labs : ['None']
Progr infl neuropathy, pork plant workers : ['None']
Poisoning, marijuana : ['None']
Disease early warning : ['None']
Unexplained deaths, elephants : ['None']
Ibuprofen, ethylene glycol poisoning : ['None']
Unidentified encephalitis : ['None']
Undiagnosed die-off, oyster : ['None']
Gonococcal disease, Chlamydia, Syphilis : ['None']
Enterobacteriaceae, drug resistant, CRE : ['None']
Measles, Malaria : ['None']
Unexplained pneumonia : ['None']
Anaplasmosis-like illness : ['None']
Asian hornet : ['None']
The Eleventh Plague : ['None']
Poxvirus, squirrels : ['None']
Announcements : ['None']
Calendar : ['None']
White mould : ['None']
Thallium poisoning : ['None']
Pulmonary fibrosis : ['None']
Contaminated stem cell : ['None']
Antibiotics, consequences of agricultural uses : ['None']
Feed po

In [7]:
# Compares all names of of a pair of outbreaks at a time and decides if they refer to the 
# same outbreak. matches is a dictionary mapping an oubreak name extraction (key) to a list 
# outbreak names that refer to the same outbreak. The results are saved in matches.json. 
# Only need to run once. Results are not perfect.
from data.stringAlignment import matchingPairs, findMatching, align, matchWords, removeExtraneous
import numpy as np
# #Uncomment to rerun matching
matches = matchingPairs(ob2Names)
# #Save results. 
with open('matches.json', 'w') as f:
    json.dump(matches, f)

0
0 : Black pod, cocoa     157 : Black pod disease  match
0 : Black pod, cocoa     729 : Black pod  match
0 : Black pod, cocoa     891 : Bud rot  match
0 : Black pod, cocoa     1026 : Coconut palm wilt  match
0 : Black pod, cocoa     1082 : Bud rot, coconut palm  match
0 : Black pod, cocoa     2237 : Black pod, Swollen shoot  match
0 : Black pod, cocoa     2309 : Lethal yellowing & bud rot, coconut palm  match
1 : Bacillus cereus, anthrax-like infection     831 : Bacillus cereus foodborne illness  match
1 : Bacillus cereus, anthrax-like infection     876 : Food poisoning, Bacillus cereus  match
1 : Bacillus cereus, anthrax-like infection     1297 : Bacillus cereus  match
1 : Bacillus cereus, anthrax-like infection     2207 : Bacillus cereus endophthalmitis  match
1 : Bacillus cereus, anthrax-like infection     2213 : Bacillus cereus infection  match
2 : Trichomonosis     2297 : Trichomoniasis  match
2 : Trichomonosis     2928 : Trichomoniasis, avian  match
3 : Blast & sheath blight, ri

8 : Necrotizing fasciitis     2500 : Streptococcus, group A  match
8 : Necrotizing fasciitis     2528 : Acute rheumatic fever  match
8 : Necrotizing fasciitis     2701 : Post-streptococcal glomerulonephritis  match
8 : Necrotizing fasciitis     2715 : Chickenpox, Scarlet fever  match
8 : Necrotizing fasciitis     2780 : Rheumatic fever  match
8 : Necrotizing fasciitis     2900 : Streptococcus,scarlet fever  match
8 : Necrotizing fasciitis     3020 : Erysipelas  match
8 : Necrotizing fasciitis     3101 : Streptococcus group A, Scarlet fever  match
8 : Necrotizing fasciitis     3117 : Streptococcus gr A, scarlet fever  match
8 : Necrotizing fasciitis     3191 : Syphilis, skin infections  match
9 : Hemorrhagic septicemia, cattle     244 : Pasteurella pneumonia  match
9 : Hemorrhagic septicemia, cattle     481 : Pneumonia, ovine  match
9 : Hemorrhagic septicemia, cattle     1090 : Hemorrhagic septicemia, elephant  match
9 : Hemorrhagic septicemia, cattle     1200 : Pasteurella multocida  m

18 : Hepatitis C     261 : Hepatitis G  match
18 : Hepatitis C     330 : Hepatitis C, HIV  match
18 : Hepatitis C     332 : Hepatitis B & C  match
18 : Hepatitis C     502 : Hepatitis C, schistosomiasis  match
18 : Hepatitis C     785 : Hepatitis, HIV/AIDS  match
18 : Hepatitis C     949 : Hepatitis C virus  match
18 : Hepatitis C     1399 : Hepatitis, viral  match
18 : Hepatitis C     1636 : Hepatitis B and C  match
18 : Hepatitis C     1645 : Viral hepatitis  match
18 : Hepatitis C     1708 : Hepatitis A, Hepatitis B, Hepatitis C  match
18 : Hepatitis C     1912 : Hepatitis B, Hepatitis C, HIV  match
18 : Hepatitis C     2211 : Hepatitis B, Hepatitis C  match
18 : Hepatitis C     2557 : Hepatitis A, Hepatitis C  match
18 : Hepatitis C     2917 : Hepatitis  match
18 : Hepatitis C     2985 : Hepatitis, undefined  match
18 : Hepatitis C     3200 : HIV/AIDS & hepatitis  match
19 : Avian influenza, human (H9N2)     29 : Avian influenza, LPAI H5  match
19 : Avian influenza, human (H9N2)   

19 : Avian influenza, human (H9N2)     2273 : Laryngotracheitis, avian  match
19 : Avian influenza, human (H9N2)     2285 : Influenza, canine  match
19 : Avian influenza, human (H9N2)     2286 : Avian influenza, H5N1, H5N6  match
19 : Avian influenza, human (H9N2)     2336 : Avian influenza, human H7N9  match
19 : Avian influenza, human (H9N2)     2348 : Avian Influenza (HPAI H5N8)  match
19 : Avian influenza, human (H9N2)     2349 : Avian influenza, H5N8  match
19 : Avian influenza, human (H9N2)     2367 : Avian influenza,H5N8  match
19 : Avian influenza, human (H9N2)     2373 : Influenza, bird-to-man  match
19 : Avian influenza, human (H9N2)     2408 : Influenza A (H1N1) virus, swine, human  match
19 : Avian influenza, human (H9N2)     2414 : Avian influenza H5N1  match
19 : Avian influenza, human (H9N2)     2416 : Avian influenza  match
19 : Avian influenza, human (H9N2)     2461 : Influenza A (H5N1)  match
19 : Avian influenza, human (H9N2)     2494 : Influenza A (H1N1), swine flu 

25 : Eastern equine encephalomyelitis     1516 : Equine encephalitis  match
25 : Eastern equine encephalomyelitis     1523 : Venezuelan equine encephalomyelitis  match
25 : Eastern equine encephalomyelitis     1629 : African Trypanosomiasis  match
25 : Eastern equine encephalomyelitis     2210 : Madariaga virus  match
25 : Eastern equine encephalomyelitis     2417 : Eastern Equine Encephalitis  match
25 : Eastern equine encephalomyelitis     2429 : Trypanosomiasis, African  match
25 : Eastern equine encephalomyelitis     2588 : African trypanosomiasis  match
25 : Eastern equine encephalomyelitis     2633 : Trypanosomiasis, control measures  match
25 : Eastern equine encephalomyelitis     2639 : Eastern equine encephalitis, West Nile virus  match
25 : Eastern equine encephalomyelitis     2755 : Eastern equine encephalitis, equine  match
25 : Eastern equine encephalomyelitis     2784 : Eastern equine encephalitis, La Crosse encephalitis  match
25 : Eastern equine encephalomyelitis     29

...

2936 : Banana bunchy-top disease     3087 : Bunchy top virus  match
2938 : Influenza, avian H7 serotype     2943 : Influenza A(H1N1) pandemic  match
2938 : Influenza, avian H7 serotype     2955 : Avian influenza (HPAI H5N1)  match
2938 : Influenza, avian H7 serotype     2994 : Avian influenza, H6N1  match
2938 : Influenza, avian H7 serotype     3011 : Influenza A(H1N2)v  match
2938 : Influenza, avian H7 serotype     3015 : Avian influenza, HPAI H5N8  match
2938 : Influenza, avian H7 serotype     3041 : avian influenza  match
2938 : Influenza, avian H7 serotype     3075 : Avian influenza, LPAI H5N2  match
2938 : Influenza, avian H7 serotype     3135 : Influenza A (H3N2)  match
2938 : Influenza, avian H7 serotype     3154 : Avian influenza,LPAI H5N2  match
2938 : Influenza, avian H7 serotype     3164 : Avian influenza, poultry vs migratory birds  match
2938 : Influenza, avian H7 serotype     3172 : Avian influenza, human  match
2938 : Influenza, avian H7 serotype     3214 : Influenza, sw

2972 : Fatal yellowing, oil palm     3251 : Big bud disease  match
2973 : Puumala virus     3177 : Puumala virus infections  match
2975
2975 : Equine Herpesvirus Type 1     2992 : Equine rhinopneumonitis, EHV-1  match
2975 : Equine Herpesvirus Type 1     3237 : Asinine herpes virus  match
2976 : White nose syndrome, bats     3076 : White-nose syndrome  match
2977 : Panama disease, banana     3211 : Banana wilt  match
2980 : Tick borne encephalitis     3006 : Dengue,DHF  match
2980 : Tick borne encephalitis     3018 : Dengue/Dengue hemorrhagic fever  match
2980 : Tick borne encephalitis     3048 : Arboviral encephalitis  match
2980 : Tick borne encephalitis     3100 : Murray Valley encephalitis virus  match
2980 : Tick borne encephalitis     3152 : West Nile virus, equines  match
2980 : Tick borne encephalitis     3157 : Yellow fever vaccination  match
2980 : Tick borne encephalitis     3166 : Tick-borne encephalitis virus  match
2980 : Tick borne encephalitis     3185 : West Nile Virus

3015 : Avian influenza, HPAI H5N8     3041 : avian influenza  match
3015 : Avian influenza, HPAI H5N8     3075 : Avian influenza, LPAI H5N2  match
3015 : Avian influenza, HPAI H5N8     3135 : Influenza A (H3N2)  match
3015 : Avian influenza, HPAI H5N8     3154 : Avian influenza,LPAI H5N2  match
3015 : Avian influenza, HPAI H5N8     3164 : Avian influenza, poultry vs migratory birds  match
3015 : Avian influenza, HPAI H5N8     3172 : Avian influenza, human  match
3015 : Avian influenza, HPAI H5N8     3214 : Influenza, swine origin  match
3015 : Avian influenza, HPAI H5N8     3219 : Influenza A (H1N1), swine, human  match
3015 : Avian influenza, HPAI H5N8     3256 : Influenza pandemic (H1N1), animal health  match
3015 : Avian influenza, HPAI H5N8     3262 : Influenza pandemic (H1N1), animal  match
3015 : Avian influenza, HPAI H5N8     3271 : Avian influenza H5N8  match
3015 : Avian influenza, HPAI H5N8     3274 : Avian Influenza  match
3015 : Avian influenza, HPAI H5N8     3275 : Avian i

3082 : Infectious mononucleosis     3151 : Lymphocryptovirus 1  match
3085 : Mayaro virus disease     3104 : Mayaro virus  match
3086 : Blast & bacterial leaf blight     3128 : Neck blast, rice  match
3086 : Blast & bacterial leaf blight     3159 : Bacterial leaf blight  match
3088 : CJD (new variant), human     3099 : Scrapie  match
3088 : CJD (new variant), human     3107 : Bovine spongiform encephalopathy (BSE)  match
3088 : CJD (new variant), human     3121 : BSE, Cattle  match
3088 : CJD (new variant), human     3124 : BSE & scrapie  match
3088 : CJD (new variant), human     3201 : CJD, optical equipment, multiple use  match
3088 : CJD (new variant), human     3249 : CJD (new variant), suspected  match
3089 : Rift Valley fever, human     3161 : Rift Valley fever, human, bovine  match
3093 : Lyssavirus     3250 : Anthrax, rabies  match
3095 : Hepatitis E     3200 : HIV/AIDS & hepatitis  match
3096 : Salmonellosis, st Paratyphi B     3244 : Cronobacteriosis, Salmonellosis  match
309

3164 : Avian influenza, poultry vs migratory birds     3271 : Avian influenza H5N8  match
3164 : Avian influenza, poultry vs migratory birds     3273 : Avian influenza (LPAI)  match
3164 : Avian influenza, poultry vs migratory birds     3274 : Avian Influenza  match
3164 : Avian influenza, poultry vs migratory birds     3275 : Avian influenza, human, H5N1, H7N9  match
3166 : Tick-borne encephalitis virus     3185 : West Nile Virus  match
3166 : Tick-borne encephalitis virus     3196 : Chikungunya,dengue  match
3168 : Undiagnosed deaths, encephalitis, Nipah virus     3184 : Nipah/Hendra - like virus  match
3169 : Inhalation anthrax     3225 : Anthrax, bovine  match
3169 : Inhalation anthrax     3228 : Anthrax letters  match
3169 : Inhalation anthrax     3250 : Anthrax, rabies  match
3171 : Canine Influenza     3173 : Influenzavirus  match
3171 : Canine Influenza     3273 : Avian influenza (LPAI)  match
3172 : Avian influenza, human     3214 : Influenza, swine origin  match
3172 : Avian 

In [9]:
#Load saved matches 
with open('matches.json', 'r') as f:
    matches = json.load(f)
#print(matches)


In [10]:
# Example of outbreak names matching 'Hepatitis A'. i is the indexes the names for 
# 'Hepatitis A'. j is the indexes the names for the outbreak being compared. 
# i,j pair gives the pair of names that lead to successful match. 
# diff is a measure of distacnce between two names being compared.
print(matches['Hepatitis A'])

{'Hepatitis A vaccination': [{'i': 0, 'j': 0, 'diff': 0}, {'i': 1, 'j': 1, 'diff': 0}, {'i': 2, 'j': 2, 'diff': 0}, {'i': 4, 'j': 3, 'diff': 0}], 'Hepatitis A & B': [{'i': 0, 'j': 0, 'diff': 0}, {'i': 1, 'j': 4, 'diff': 0}, {'i': 4, 'j': 2, 'diff': 0}], 'Hepatitis A vaccine': [{'i': 1, 'j': 5, 'diff': 0}, {'i': 4, 'j': 4, 'diff': 0}], 'Hepatitis, viral': [{'i': 0, 'j': 0, 'diff': 0}], 'Leptospirosis, hepatitis A': [{'i': 0, 'j': 3, 'diff': 0}, {'i': 4, 'j': 4, 'diff': 0}], 'Hepatitis A & E': [{'i': 0, 'j': 0, 'diff': 0}, {'i': 2, 'j': 2, 'diff': 0}], 'Viral hepatitis': [{'i': 0, 'j': 1, 'diff': 0}], 'Hepatitis A, Hepatitis B, Hepatitis C': [{'i': 0, 'j': 0, 'diff': 0}, {'i': 3, 'j': 6, 'diff': 0}, {'i': 4, 'j': 9, 'diff': 0}], 'Hepatitis A, Hepatitis E': [{'i': 0, 'j': 0, 'diff': 0}, {'i': 2, 'j': 2, 'diff': 0}], 'Epidemic jaundice': [{'i': 0, 'j': 0, 'diff': 0}, {'i': 2, 'j': 2, 'diff': 0}], 'Hepatitis A, Hepatitis C': [{'i': 0, 'j': 0, 'diff': 0}, {'i': 1, 'j': 4, 'diff': 0}, {'i': 3

In [14]:
# number of pairs of matching outbreaks 
nMatch = np.sum(len(m) for m in matches.values())
print('Number of matches: '+ str(nMatch))

Number of matches: 47491


/var/folders/lj/6gfrhbf15_1_dhvth8xrbgjr0000gn/T/ipykernel_10761/2671396106.py:2: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  nMatch = np.sum(len(m) for m in matches.values())


In [50]:
# Find groups of outbreak strings that refer to the same outbreak as maximal cliques in the 
# graph created from matches
from networkx import from_numpy_array, find_cliques
import numpy as np
mat = np.zeros((len(res),len(res)))
OB = np.array(list(matches.keys()))
for (i, (k,v)) in enumerate(matches.items()):
    #print(i,k,v)
    for vv in v.keys():
        #pdb.set_trace()
        mat[i, np.where(OB==vv)[0]]=1
G = from_numpy_array(mat)
C = find_cliques(G)
CC = []
for c in C:
    CC.append(OB[np.array(c)])
print(CC)

set()